# Plot: Hotzones at 17h on weekdays

Import modules

In [9]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
import plotly.graph_objects as go

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [6]:
# Load data
nyc_trip_clusters = pd.read_parquet('/content/drive/MyDrive/_JEDHA_DATASCIENCE/UNSUPERVISED_ML/project_uber/uber-trip-data/trip_data_with_clusters.parquet')

In [4]:
nyc_trip_clusters.head()

Lat      Lon    Base  hour  day weekday  month  LocationID Borough  \
0  40.7366 -73.9906  B02512     0    1  Friday      8         192  Queens   
1  40.7260 -73.9918  B02512     0    1  Friday      8         192  Queens   
2  40.7209 -74.0507  B02512     0    1  Friday      8         192  Queens   
3  40.7387 -73.9856  B02512     0    1  Friday      8         192  Queens   
4  40.7323 -74.0077  B02512     0    1  Friday      8         192  Queens   

              Zone  
0  Queensboro Hill  
1  Queensboro Hill  
2  Queensboro Hill  
3  Queensboro Hill  
4  Queensboro Hill

In [36]:
nyc_trip_clusters.size

49877597

In [41]:
nyc_sample = nyc_trip_clusters.sample(1800000)

Create function to plot hotzones with dropdown

In [42]:
def plot_hotzones_weekday_buttons(trip_data):
    """
    Efficient scatter_mapbox plot with weekday buttons (Mon–Fri) for fixed hour (17:00).
    """

    trip_data['dbscan_cluster'] = trip_data['dbscan_cluster'].astype(int)
    selected_hour = 17
    weekdays = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday']
    cmax = trip_data['dbscan_cluster'].max()

    traces = []
    for weekday in weekdays:
        df = trip_data[
            (trip_data['weekday'] == weekday) &
            (trip_data['hour'] == selected_hour) &
            (trip_data['dbscan_cluster'] != -1)
        ]

        traces.append(go.Scattermapbox(
            lat=df['Lat'],
            lon=df['Lon'],
            mode='markers',
            marker=dict(
                size=7,
                color=df['dbscan_cluster'],
                colorscale='Plasma',
                cmin=0,
                cmax=cmax,
                showscale=True,
                colorbar=dict(title="Cluster ID")
            ),
            name=weekday,
            text=df['Zone'],
            customdata=df[['Zone', 'Borough']],
            hovertemplate="<b>Zone:</b> %{customdata[0]}<br><b>Borough:</b> %{customdata[1]}<extra></extra>",
            visible=(weekday == 'Monday')  # Default
        ))

    # Create visibility toggle buttons
    buttons = [
        dict(
            label=weekday,
            method="update",
            args=[
                {"visible": [j == i for j in range(len(weekdays))]},
                {"title": f"Hotzones in New York on {weekday} at 17:00"}
            ]
        )
        for i, weekday in enumerate(weekdays)
    ]

    # Build figure layout
    fig = go.Figure(data=traces)
    fig.update_layout(
        mapbox_style="open-street-map",
        mapbox_center={"lat": 40.7128, "lon": -74.0060},
        mapbox_zoom=10,
        height=700,
        width=1200,
        title="Hotzones in New York on Monday at 17:00",
        title_x=0.5,
        updatemenus=[dict(
            buttons=buttons,
            direction="right",
            x=0.01,
            xanchor="left",
            y=1.08,
            yanchor="top",
            showactive=True
        )]
    )

    return fig


In [43]:
fig = plot_hotzones_weekday_buttons(nyc_sample)
fig.show()

In [44]:
fig.write_html('/content/drive/MyDrive/_JEDHA_DATASCIENCE/UNSUPERVISED_ML/project_uber/uber-trip-data/hotzones_nyc_weekdays_17.html')